# Greenland peripheral glacier automated terminus detection image download and pre-processing

By Jukes Liu (jukes.liu@boisestate.edu)

_Last modified 06-12-2020._

# 1) Set-up: import necessary packages, set paths, and glaciers of interest

In [1]:
import numpy as np
import pandas as pd
import scipy
import math

import subprocess
import os
import shutil

import cv2
from PIL import Image
import matplotlib.image as mpimg
import matplotlib.pyplot as plt

# geospatial packages
import fiona
import geopandas as gpd
from shapely.geometry import Polygon, Point
import shapely
import rasterio

# Enable fiona KML file reading driver
gpd.io.file.fiona.drvsupport.supported_drivers['KML'] = 'rw'

# Set base paths
basepath='/home/jukes/Documents/Sample_glaciers/' # folder containing the box shapefile and info
downloadpath = '/media/jukes/jukes1/LS8aws/' # folder to contain the downloaded images

# import necessary functions from automated-glacier-terminus.py
os.chdir('/home/jukes/automated-glacier-terminus') #import necessary functions:
from automated_terminus_functions import distance, resize_pngs

#### Enter peripheral glaciers of interest by their 3-digit BoxIDs:

These BoxIDs will be used to refer to the files for the glacier and will be used in generation of new file names. 

In [117]:
BoxIDs = []
boxes = list(map(str, np.arange(69, 296, 6)))
for BoxID in boxes:
    BoxID = BoxID.zfill(3)
    BoxIDs.append(BoxID)
print(BoxIDs)

['069', '075', '081', '087', '093', '099', '105', '111', '117', '123', '129', '135', '141', '147', '153', '159', '165', '171', '177', '183', '189', '195', '201', '207', '213', '219', '225', '231', '237', '243', '249', '255', '261', '267', '273', '279', '285', '291']


#### Create new folders corresponding to these glaciers:

Change _boxespath_ to the folder with the glacier terminus box shapefiles and _RGIpath_ to the folder containing the Randoplh Glacier Inventory (RGI) full glacier outline shapefiles.

In [118]:
# create new BoxID folders 
for BoxID in BoxIDs:
    # create folder in Sample_glaciers
    if os.path.exists(basepath+'Box'+BoxID)==True:
#         shutil.rmtree(basepath+'Box'+BoxID)
        print("Path exists already in Sample_glaciers for Box", BoxID)
    else:
        os.mkdir(basepath+'Box'+BoxID)
        
    # move terminus box shapefile into the new folder
    ID = int(BoxID) # make into an integer in order to grab the .shp files from Boxes_individual
    boxespath = '/media/jukes/jukes1/Boxes_individual/'
    for file in os.listdir(boxespath):
        if file.startswith(str(ID)):
            if len(file) == len(str(ID))+4:
#             if file.endswith('.dbf') or file.endswith('.prj') or file.endswith('.qpj') or file.endswith('.shx') or file.endswith('.shp'):
                shutil.copyfile(boxespath+file, basepath+'Box'+BoxID+'/Box'+BoxID+file[-4:])

    # move RGI glacier outline into the new folder
    RGIpath = '/media/jukes/jukes1/RGI_shps/'
    for file in os.listdir(RGIpath):
        if file.startswith('BoxID_'+str(ID)):
            shutil.copyfile(RGIpath+file, basepath+'Box'+BoxID+'/RGI_Box'+BoxID+file[-4:])
            
    # make a new folder for the glacier in the download folder
    if os.path.exists(downloadpath+'/Box'+BoxID)==True:
        print("Path exists already in LS8aws for Box", BoxID)
    else:
        os.mkdir(downloadpath+'/Box'+BoxID)

Path exists already in Sample_glaciers for Box 105
Path exists already in LS8aws for Box 105
Path exists already in Sample_glaciers for Box 111
Path exists already in LS8aws for Box 111
Path exists already in Sample_glaciers for Box 135
Path exists already in LS8aws for Box 135
Path exists already in Sample_glaciers for Box 141
Path exists already in LS8aws for Box 141
Path exists already in Sample_glaciers for Box 147
Path exists already in LS8aws for Box 147
Path exists already in Sample_glaciers for Box 165
Path exists already in LS8aws for Box 165
Path exists already in Sample_glaciers for Box 171
Path exists already in LS8aws for Box 171
Path exists already in Sample_glaciers for Box 195
Path exists already in LS8aws for Box 195
Path exists already in Sample_glaciers for Box 201
Path exists already in LS8aws for Box 201
Path exists already in Sample_glaciers for Box 213
Path exists already in LS8aws for Box 213
Path exists already in Sample_glaciers for Box 219
Path exists already

# 2) Find all the Landsat Path Row identifiers that overlap the glaciers

This step requires the WRS-2_bound_world.kml file containing the footprints of all the Landsat scene boundaries available through the USGS (https://www.usgs.gov/land-resources/nli/landsat/landsat-shapefiles-and-kml-files). To check if they overlap the glacier terminus box shapefiles, the box shapefiles must be reprojected into WRS84 coordinates (ESPG: 4326) using GDAL command line command:

    ogr2ogr -f "ESRI Shapefile" -t_srs EPSG:NEW_EPSG_NUMBER -s_srs EPSG:OLD_EPSG_NUMBER output.shp input.shp

In [72]:
# reproject
for BoxID in BoxIDs:
    boxpath = basepath+"Box"+BoxID+"/Box"+BoxID            
    rp = "ogr2ogr --config GDAL_DATA /usr/share/gdal/ -f 'ESRI Shapefile' -t_srs EPSG:4326 -s_srs EPSG:3413 "+boxpath+"_WRS.shp "+boxpath+".shp"
    subprocess.call(rp, shell=True)
    print(BoxID)

067
073
079
085
091
097
103
109
115
121
127
133
139
145
151
157
163
169
175
181
187
193
199
205
211
217
223
229
235
241
247
253
259
265
271
277
283
289
295
301


In [73]:
# Grab the boxes' WRS84 coordinates
box_points = {}
for BoxID in BoxIDs:
    boxpath = basepath+"Box"+BoxID+"/Box"+BoxID; termbox = fiona.open(boxpath+'_WRS.shp')
    box = termbox.next()
    box_geom= box.get('geometry'); box_coords = box_geom.get('coordinates')[0]  
    points = [] # to hold the vertices
    for coord_pair in box_coords:
        lat = coord_pair[0]; lon = coord_pair[1]
        #create shapely pyoints and append to points list
        point = shapely.geometry.Point(lat, lon)
#         print(point)
        points.append(point)
    box_points.update({BoxID: points}); print("Box"+BoxID)

Box067
Box073
Box079
Box085
Box091
Box097
Box103
Box109
Box115
Box121
Box127
Box133
Box139
Box145
Box151
Box157
Box163
Box169
Box175
Box181
Box187
Box193
Box199
Box205
Box211
Box217
Box223
Box229
Box235
Box241
Box247
Box253
Box259
Box265
Box271
Box277
Box283
Box289
Box295
Box301


/home/jukes/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: FionaDeprecationWarning: Collection.__next__() is buggy and will be removed in Fiona 2.0. Switch to `next(iter(collection))`.
  """


In [74]:
#open the kml file with the pathrow bounds as WRS
WRS = fiona.open(basepath+'WRS-2_bound_world.kml', driver='KML')

### Loop through all the scene footprints and stores those that overlap ALL of your shapefile vertices:

In [75]:
#create lists to hold the paths and rows and BoxIDs
paths = []; rows = []; boxes = []

#loop through all features in the WRS .kml:
for feature in WRS:
    #create shapely polygons with the pathrow bounds
    coordinates = feature['geometry']['coordinates'][0]
    coords = [xy[0:2] for xy in coordinates]
#     print(coords)
    pathrow_poly = Polygon(coords)
    #grab the path and row name
    pathrowname = feature['properties']['Name']  
    path = pathrowname.split('_')[0]; row = pathrowname.split('_')[1]
#     print(path, row)
    
    #for each feature, loop through each of the box_points
    for BoxID in box_points:
        #create a counter for number of box_points in the pathrow_geom:
        box_points_in = 0
        
        points = box_points.get(BoxID)
        for i in range(0, len(points)):
            point = points[i]
            #if the pathrow shape contains the point
            if point.within(pathrow_poly):
#                 print("Found")
                #append the counter
                box_points_in = box_points_in+1
#         print(box_points_in)
        if box_points_in == 5:
            #save that path row and boxID
            paths.append('%03d' % int(path)); rows.append('%03d' % int(row))
            boxes.append(BoxID)

boxes_pr_df = pd.DataFrame(list(zip(boxes, paths, rows)), columns=['BoxID','Path', 'Row'])
boxes_pr_df = boxes_pr_df.sort_values(by='BoxID')
boxes_pr_df

BoxID Path  Row
1     067  233  018
8     067  232  018
2     073  233  018
9     073  232  018
3     079  233  018
..    ...  ...  ...
104   295  231  013
105   301  231  013
97    301  230  014
102   301  232  013
106   301  230  013

[107 rows x 3 columns]

#### Write it to a csv file:

In [76]:
# change the filename as desired
PR_FILENAME = 'LS_pathrows_SE_2.csv'
boxes_pr_df.to_csv(path_or_buf = basepath+PR_FILENAME, sep=',')

# 3) Download metadata (MTL.txt) files for all available images over glaciers

Bulk download Landsat-8 images and metadata stored on the Amazon Web Services cloud (s3 bucket) over a region of interest using the Amazon Web Services command line interface. Follow instructions at https://docs.aws.amazon.com/cli/latest/userguide/cli-chap-install.html to get aws commands onto your command terminal. The syntax for grabbing an individual metadata file is as follows:

     aws --no-sign-request s3 cp s3://landsat-pds/c1/L8/path/row/LC08_XXXX_pathrow_yyyyMMdd_01_T1/LC08_XXXX_pathrow_yyyyMMdd_01_T1_MTL.txt /path_to/output/

Access https://docs.opendata.aws/landsat-pds/readme.html to learn more.

#### Download the metadatafiles into Path_Row folders created using:

    aws --no-sign-request s3 cp s3://landsat-pds/c1/L8/031/005/ Output/path/LS8aws/Path031_Row005/ --recursive --exclude "*" --include "*MTL.txt" 

In [77]:
# use the csv file from the previous step to access all the data in the folders:
boxes_pr_df = pd.read_csv(basepath+PR_FILENAME, dtype=str)
boxes_pr_df = boxes_pr_df.set_index('BoxID'); boxes_pr_df

Unnamed: 0 Path  Row
BoxID                     
067            1  233  018
067            8  232  018
073            2  233  018
073            9  232  018
079            3  233  018
...          ...  ...  ...
295          104  231  013
301          105  231  013
301           97  230  014
301          102  232  013
301          106  230  013

[107 rows x 3 columns]

In [78]:
#Loop through the dataframe with your path row combinations:
for index, row in boxes_pr_df.iterrows():
    #grab the path row names and set the folder name
    path = row['Path']; row = row['Row']; folder_name = 'Path'+path+'_Row'+row+'_c1'

    #set path to access the image on the amazon cloud:
    bp_in = 's3://landsat-pds/c1/L8/'; totalp_in = bp_in+path+'/'+row+'/'
    #set output path for the downloaded files:
    bp_out = downloadpath+folder_name+'/'; print(bp_out)
    
    #create Path_Row folders and do the download if they don't exist already to hold the metadata
    if os.path.exists(bp_out):
        print(folder_name, " EXISTS ALREADY. SKIP.")
    else:
        os.mkdir(bp_out)
        print(folder_name+" directory made")
        command = 'aws --no-sign-request s3 cp '+totalp_in+' '+bp_out+' --recursive --exclude "*" --include "*MTL.txt"'
        print(command)

        #call the command line that downloads the metadata files using aws
        subprocess.call(command, shell=True)

/media/jukes/jukes1/LS8aws/Path233_Row018_c1/
Path233_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path232_Row018_c1/
Path232_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path233_Row018_c1/
Path233_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path232_Row018_c1/
Path232_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path233_Row018_c1/
Path233_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path232_Row018_c1/
Path232_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path233_Row018_c1/
Path233_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path232_Row018_c1/
Path232_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path233_Row018_c1/
Path233_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path232_Row018_c1/
Path232_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path001_Row018_c1/
Path001_Row018_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path001_Row017_c

/media/jukes/jukes1/LS8aws/Path232_Row013_c1/
Path232_Row013_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path231_Row013_c1/
Path231_Row013_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path232_Row014_c1/
Path232_Row014_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path231_Row014_c1/
Path231_Row014_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path230_Row014_c1/
Path230_Row014_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path232_Row013_c1/
Path232_Row013_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path232_Row013_c1/
Path232_Row013_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path231_Row014_c1/
Path231_Row014_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path230_Row014_c1/
Path230_Row014_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path231_Row013_c1/
Path231_Row013_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path231_Row013_c1/
Path231_Row013_c1  EXISTS ALREADY. SKIP.
/media/jukes/jukes1/LS8aws/Path230_Row014_c

# 4) Determine how cloudy the images are using the LS quality band files subset to terminus box

Use gdalwarp commands and the __vsicurl__ link to download subset of the quality band we will use to determine cloud cover:

    gdalwarp -cutline path_to_shp.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/031/005/imagename/imagename_BQA.TIF path_to_subsetBQA.TIF
    
These will need to go into the newly created BoxID folders because the subset of the same image for different boxes will be different. We will need to reproject the shapefiles into UTM to match the LS8 bands. We must grab the UTM zones from the metadata files downloaded and fill in the following syntax:
    
    ogr2ogr -f "ESRI Shapefile" -t_srs EPSG:326zone -s_srs EPSG:3413 output.shp input.shp

In [79]:
zones = {}; zone_df = []

#Loop through the dataframe with your path row combinations:
for index, row in boxes_pr_df.iterrows():
    path = row['Path']; row = row['Row']; BoxID = str(index); folder_name = 'Path'+path+'_Row'+row+'_c1'
    
    #set path to path row folders to grab scenes from and output path according to each of the BoxIDs
    pr_folderpath = downloadpath+folder_name+'/'
    
    #set shapefile path for each BoxID
    pathtoshp = basepath+"Box"+BoxID+"/Box"+BoxID
    
    #if there are files in the folder:
    if len(os.listdir(pr_folderpath)) > 0:
        #grab UTM Zone from the first metadata file in the pr_folderpath
        mtl_scene = os.listdir(pr_folderpath)[0]
        mtl = open(pr_folderpath+mtl_scene+'/'+mtl_scene+'_MTL.txt', 'r')
        
        #loop through each line in metadata to find the UTM ZONE
        for line in mtl:
            variable = line.split("=")[0]
            if ("UTM_ZONE" in variable): 
                #save it:
                zone = '%02d' % int(line.split("=")[1][1:-1])
                zones.update({folder_name: zone}); zone_df.append(zone)
                
        #reproject shapefile(s) into UTM
        zone = zones[folder_name]
        rp_shp = 'ogr2ogr -f "ESRI Shapefile" -t_srs EPSG:326'+zone+' -s_srs EPSG:4326 '+pathtoshp+"_UTM_"+zone+".shp "+pathtoshp+"_WRS.shp"
        subprocess.call(rp_shp, shell=True)
    #if not, append nan to zone and do nothing
    else:
        zone_df.append(np.nan)
        
    #grab the names of the LS8 scenes from the downloaded metadatafiles using os.listdir() in the Path_Row folders
    scenes = os.listdir(pr_folderpath)

    for scene in scenes:
        #if the file grabbed does correspond to a Landsat scene (starts with LC08):
        if len(scenes) > 0 and scene.startswith("LC08"):            
            #set path to reprojected box shp
            pathtoshp_rp = pathtoshp+'_UTM_'+zones[folder_name]
            
            #set path to the quality band (BQA.TIF) in the cloud using the scenename
            pathtoBQA = '/vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/'+path+'/'+row+'/'+scene+"/"+scene+"_BQA.TIF"
            subsetout = pr_folderpath+scene+"/"+scene+'_BQA_Box'+BoxID+'.TIF'

            #Check download command syntax
            BQA_dwnld_cmd = 'gdalwarp -cutline '+pathtoshp_rp+'.shp -crop_to_cutline '+pathtoBQA+' '+subsetout

            #When you've checked everything, uncomment the following to run:
            subprocess.call(BQA_dwnld_cmd, shell=True)
            print(scene+'_BQA_Box'+BoxID+'.TIF subset downloaded')

boxes_pr_df['Zone'] = zone_df
print("Done.")

LC08_L1TP_233018_20181104_20181104_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1GT_233018_20190312_20190312_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20150621_20170407_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20130903_20170502_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20190803_20190803_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20180410_20180410_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20190803_20190819_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20191022_20191030_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20190819_20190902_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20151128_20170401_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20171219_20171219_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20160420_20170326_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20180512_20180517_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20161130_20170317_01_

LC08_L1TP_233018_20170813_20170825_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20160404_20170327_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1GT_233018_20200126_20200126_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1GT_233018_20190123_20190123_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20190920_20190926_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20160506_20170325_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20161029_20170319_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1GT_233018_20170626_20170626_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20170829_20170829_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1GT_233018_20180104_20180104_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20160911_20170321_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20180528_20180528_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20190819_20190819_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_233018_20191022_20191022_01_

LC08_L1TP_232018_20180302_20180302_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20200220_20200220_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20140627_20170421_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1GT_232018_20180708_20180708_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1GT_232018_20171009_20171009_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20170603_20170615_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20170705_20170705_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20180724_20180731_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20170619_20170619_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20170603_20170603_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20161022_20170319_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20151004_20170403_01_T1_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20191116_20191116_01_RT_BQA_Box067.TIF subset downloaded
LC08_L1TP_232018_20140510_20170422_01_

LC08_L1TP_233018_20190515_20190521_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20160826_20170321_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20170930_20171013_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20190718_20190718_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20180426_20180426_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20200110_20200110_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20140415_20180426_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20181019_20181019_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20180917_20180928_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20150707_20170407_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20180205_20180221_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1GT_233018_20180816_20180816_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20190515_20190515_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20191225_20200110_01_

LC08_L1GT_233018_20190224_20190224_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20160607_20170324_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20140922_20170419_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20170610_20170610_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1GT_233018_20171101_20171101_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1GT_233018_20191107_20191107_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20150504_20170409_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20200227_20200313_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20200314_20200325_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20170712_20170712_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20170525_20170525_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20190328_20190404_01_T1_BQA_Box073.TIF subset downloaded
LC08_L1GT_233018_20190702_20190702_01_RT_BQA_Box073.TIF subset downloaded
LC08_L1TP_233018_20180205_20180205_01_

...

LC08_L1TP_231013_20191024_20191030_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20170511_20170525_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20140519_20170422_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20170714_20170714_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1GT_231013_20170916_20170917_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20160625_20170323_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20150810_20170406_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20160711_20170323_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20150725_20170406_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20170831_20170831_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20140823_20170420_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20160812_20170322_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20180802_20180802_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_231013_20160828_20170321_01_

LC08_L1GT_230014_20180421_20180421_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1GT_230014_20190424_20190424_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1GT_230014_20170925_20170925_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230014_20190814_20190814_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230014_20191017_20191017_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1GT_230014_20191118_20191118_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230014_20170909_20170909_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1GT_230014_20181115_20181115_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230014_20160704_20170323_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_230014_20150702_20170407_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1GT_230014_20171011_20171011_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230014_20161024_20170318_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1GT_230014_20190611_20190611_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230014_20180608_20180608_01_

LC08_L1TP_232013_20170806_20170806_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20190609_20190609_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20180825_20180829_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1GT_232013_20190217_20190217_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1GT_232013_20170705_20170705_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20150614_20170407_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20150918_20170404_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20170822_20170822_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20130928_20180528_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20170603_20170603_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1GT_232013_20180318_20180318_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20140729_20170420_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20170603_20170615_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_232013_20170619_20170619_01_

LC08_L1TP_230013_20140221_20170425_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20180912_20180927_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20190307_20190307_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20170925_20170925_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20150718_20170406_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20170824_20170824_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20190323_20190323_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20181014_20181014_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20190611_20190619_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20170808_20170823_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1GT_230013_20170621_20170621_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20170520_20170525_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20170605_20170606_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1GT_230013_20190219_20190219_01_

LC08_L1GT_230013_20190627_20190627_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20140816_20170420_01_T1_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20190408_20190408_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20200613_20200613_01_RT_BQA_Box301.TIF subset downloaded
LC08_L1TP_230013_20181030_20181115_01_T1_BQA_Box301.TIF subset downloaded
Done.


#### Re-save csv file with the UTM zone information

In [80]:
# change name as desired
PR_FILENAME = 'LS_pathrows_SE_2.csv'
boxes_pr_df.to_csv(path_or_buf = basepath+PR_FILENAME, sep=',')

# 5) Create buffer zone around terminus boxes and rasterize/subset terminus boxes (used for cropping and masknig later on)

The following code pulls the buffer distances around the terminus boxes from an existing .csv file with the exported attributes tables for the peripheral glacier terminus boxes. These buffer distances will be used to create a buffer zone to subset the Landsat scenes.

In [81]:
buffers = []
mindimensions = []
#Calculate a buffer distance around the terminus box using the UTM projected boxes
for BoxID in BoxIDs:
    buff_distances = []
    mindims = []
    for file in os.listdir(basepath+'Box'+BoxID+'/'):
        if 'UTM' in file and '.shp' in file and "Box" in file:
            boxpath = basepath+"Box"+BoxID+"/"+file  
            termbox = fiona.open(boxpath)
            #grab the box feature:
            box = termbox.next(); box_geom= box.get('geometry'); box_coords = box_geom.get('coordinates')[0]
            points = []
            for coord_pair in box_coords:
                lat = coord_pair[0]; lon = coord_pair[1]; points.append([lat, lon])
            
            #Calculate distance between 1 and 2 and distance between 2 and 3 and pick the longer one
            coord1 = points[0]; coord2 = points[1]; coord3 = points[2]   
            dist1 = distance(coord1[0], coord1[1], coord2[0], coord2[1]);
            dist2 = distance(coord2[0], coord2[1], coord3[0], coord3[1])  
            buff_dist = int(np.max([dist1, dist2]))
            buff_distances.append(buff_dist) 
            mindim = int(np.min([dist1, dist2]))
            mindims.append(int(mindim/15.0))
    buffer = buff_distances[0]; buffers.append(buffer); minimum = mindims[0]; mindimensions.append(minimum)
buff_df = pd.DataFrame(list(zip(BoxIDs, buffers, mindimensions)), columns=['BoxID', 'Buff_dist_m', 'min_dim_px'])
buff_df

/home/jukes/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:12: FionaDeprecationWarning: Collection.__next__() is buggy and will be removed in Fiona 2.0. Switch to `next(iter(collection))`.
  if sys.path[0] == '':


BoxID  Buff_dist_m  min_dim_px
0    067         1648          54
1    073         1261          63
2    079          861          33
3    085          614          23
4    091         1104          40
5    097          930          41
6    103          907          30
7    109          810          21
8    115         2301          73
9    121         1352          70
10   127          709          36
11   133         1184          65
12   139          686          28
13   145         1064          21
14   151         1087          41
15   157          605          19
16   163         1381          36
17   169         1069          46
18   175          769          26
19   181         1313          48
20   187         1196          33
21   193         1509          47
22   199         1601          96
23   205         1903          53
24   211          576          17
25   217         1030          58
26   223          837          18
27   229         1096          62
28   235         1643          57
29   241          793          30
30   247         1939          76
31   253         1868         120
32   259         2965         155
33   265          971          64
34   271         2087         115
35   277         1379          55
36   283         1511          60
37   289         3154         125
38   295         1538          51
39   301          738          24

In [82]:
buff_df.to_csv(basepath+'Buffdist_SE_2.csv')

The next section creates a buffer zone shapefile using GDAL command **ogr2ogr** with the following syntax:

    ogr2ogr Buffer###.shp path_to_terminusbox###.shp  -dialect sqlite -sql "SELECT ST_Buffer(geometry, buffer_distance) AS geometry,*FROM 'Box###'" -f "ESRI Shapefile"

In [83]:
for index, row in buff_df.iterrows():
    BoxID = row['BoxID']
    buff_dist = str(row['Buff_dist_m'])
    
    # Set path to the terminus box shapefiles
    terminusbox_path = basepath+"Box"+BoxID+"/Box"+BoxID+".shp"
    outputbuffer_path = basepath+"Box"+BoxID+"/Buffer"+BoxID+".shp"
    
    # Set buffer command and print to check it
    buffer_cmd = 'ogr2ogr '+outputbuffer_path+" "+terminusbox_path+' -dialect sqlite -sql "SELECT ST_Buffer(geometry, '+buff_dist+") AS geometry,*FROM 'Box"+BoxID+"'"+'" -f "ESRI Shapefile"'
    print(buffer_cmd)
    
    subprocess.call(buffer_cmd, shell=True) 
    print("Box"+BoxID)

ogr2ogr /home/jukes/Documents/Sample_glaciers/Box067/Buffer067.shp /home/jukes/Documents/Sample_glaciers/Box067/Box067.shp -dialect sqlite -sql "SELECT ST_Buffer(geometry, 1648) AS geometry,*FROM 'Box067'" -f "ESRI Shapefile"
Box067
ogr2ogr /home/jukes/Documents/Sample_glaciers/Box073/Buffer073.shp /home/jukes/Documents/Sample_glaciers/Box073/Box073.shp -dialect sqlite -sql "SELECT ST_Buffer(geometry, 1261) AS geometry,*FROM 'Box073'" -f "ESRI Shapefile"
Box073
ogr2ogr /home/jukes/Documents/Sample_glaciers/Box079/Buffer079.shp /home/jukes/Documents/Sample_glaciers/Box079/Box079.shp -dialect sqlite -sql "SELECT ST_Buffer(geometry, 861) AS geometry,*FROM 'Box079'" -f "ESRI Shapefile"
Box079
ogr2ogr /home/jukes/Documents/Sample_glaciers/Box085/Buffer085.shp /home/jukes/Documents/Sample_glaciers/Box085/Box085.shp -dialect sqlite -sql "SELECT ST_Buffer(geometry, 614) AS geometry,*FROM 'Box085'" -f "ESRI Shapefile"
Box085
ogr2ogr /home/jukes/Documents/Sample_glaciers/Box091/Buffer091.shp /ho

Box277
ogr2ogr /home/jukes/Documents/Sample_glaciers/Box283/Buffer283.shp /home/jukes/Documents/Sample_glaciers/Box283/Box283.shp -dialect sqlite -sql "SELECT ST_Buffer(geometry, 1511) AS geometry,*FROM 'Box283'" -f "ESRI Shapefile"
Box283
ogr2ogr /home/jukes/Documents/Sample_glaciers/Box289/Buffer289.shp /home/jukes/Documents/Sample_glaciers/Box289/Box289.shp -dialect sqlite -sql "SELECT ST_Buffer(geometry, 3154) AS geometry,*FROM 'Box289'" -f "ESRI Shapefile"
Box289
ogr2ogr /home/jukes/Documents/Sample_glaciers/Box295/Buffer295.shp /home/jukes/Documents/Sample_glaciers/Box295/Box295.shp -dialect sqlite -sql "SELECT ST_Buffer(geometry, 1538) AS geometry,*FROM 'Box295'" -f "ESRI Shapefile"
Box295
ogr2ogr /home/jukes/Documents/Sample_glaciers/Box301/Buffer301.shp /home/jukes/Documents/Sample_glaciers/Box301/Box301.shp -dialect sqlite -sql "SELECT ST_Buffer(geometry, 738) AS geometry,*FROM 'Box301'" -f "ESRI Shapefile"
Box301


The terminus box shapefiles are then rasterized (to be used as a mask during the WTMM filering) using the GDAL **gdal_rasterize** command and subset to the buffer zone using the GDAL **gdalwarp** command using the following syntax:

1) Rasterize

    gdal_rasterize -burn 1.0 -tr x_resolution y_resolution -a_nodata 0.0 path_to_terminusbox.shp path_to_terminusbox_raster.TIF

The x_resolution and y_resolution are set to be 15.0 (meters) to match the Landsat B8 resolution.
    
2) Subset

    gdalwarp -cutline path_to_Buffer###.shp -crop_to_cutline path_to_terminusbox_raster.TIF path_to_subset_raster_cut.TIF

In [84]:
for index, row in buff_df.iterrows():
    BoxID = row['BoxID']
    # Set path to the terminus box shapefiles
    terminusbox_path = basepath+"Box"+BoxID+"/Box"+BoxID+".shp"
    buffer_path = basepath+"Box"+BoxID+"/Buffer"+BoxID+".shp"
    
    # output raster path:
    terminusraster_path = basepath+"Box"+BoxID+"/Box"+BoxID+".TIF"
    cutraster_path = basepath+"Box"+BoxID+"/Box"+BoxID+"_raster_cut.TIF"
    
    # Set commands and print to check
    rasterize_cmd = 'gdal_rasterize -burn 1.0 -tr 15.0 15.0 -a_nodata 0.0 '+terminusbox_path+' '+terminusraster_path
    subsetbuffer_cmd = 'gdalwarp -cutline '+buffer_path+' -crop_to_cutline '+terminusraster_path+" "+cutraster_path
    
    # RASTERIZE & SUBSET
    subprocess.call(rasterize_cmd, shell=True)
    subprocess.call(subsetbuffer_cmd, shell=True)
    
    print("Box"+BoxID)

Box067
Box073
Box079
Box085
Box091
Box097
Box103
Box109
Box115
Box121
Box127
Box133
Box139
Box145
Box151
Box157
Box163
Box169
Box175
Box181
Box187
Box193
Box199
Box205
Box211
Box217
Box223
Box229
Box235
Box241
Box247
Box253
Box259
Box265
Box271
Box277
Box283
Box289
Box295
Box301


# 6) Download non-cloudy images

To threshold out cloudy images, we will find the number of pixels in our shapefile region that correspond to a cumulative pixel value of > __25000__. If the number of pixels with values above this threshold is greater than our % threshold, we won't download the image. 

__EDITED: We'll also filter out those images along the border that cutoff through your shapefile region. These will have a designated fill value of 1.__

Set cloudy and fill thresholds:

In [85]:
# Set cloud cover threshold
cpercent_thresh = 20.0

# Set fill percent threshold
fpercent_thresh = 60.0

# Set BQA pixel value threshold
BQA_thresh = 4096.0

Set LS bands to download:

In [86]:
#SET your desired Landsat bands here
bands = [8] # panchromatic
# bands = [2, 3, 4] # multispectral 

### Download the images that pass these thresholds:

In [87]:
#Loop through the dataframe with your path row combinations:
for index, row in boxes_pr_df.iterrows():
    #grab the path row names and set the folder name
    path = row['Path']; zone = row['Zone']; row = row['Row']; BoxID = index; 
    folder_name = 'Path'+path+'_Row'+row+'_c1'
    
    #set path to path row folders to grab BQA files from
    pr_folderpath = downloadpath+folder_name+'/'
    
    #Output BoxID folderpath and create BoxID folders
    bp_out = downloadpath+'Box'+BoxID+'/'
    
    if os.path.exists(bp_out):
        print("Box"+BoxID, " EXISTS ALREADY. SKIP.")
    else:
        os.mkdir(bp_out)
        print("Box"+BoxID+" directory made")
                      
    #set path to the buffer zones for final subsetting:
    pathtobuffer = basepath+'Box'+BoxID+'/Buffer'+BoxID
#     pathtoshp_rp = basepath+'Box'+BoxID+'/Box'+BoxID+'_UTM_'+zone+'.shp'
    
    #REPROJECT BUFFER SHAPE
    if len(os.listdir(pr_folderpath)) > 0:
#         print(zone)
        rp_shp = 'ogr2ogr -f "ESRI Shapefile" -t_srs EPSG:326'+zone+' -s_srs EPSG:3413 '+pathtobuffer+"_UTM_"+zone+".shp "+pathtobuffer+".shp"
#         print(rp_shp)
        subprocess.call(rp_shp, shell=True)

    #loop through all the BQA files in the path_row folders:
    for scene in os.listdir(pr_folderpath):
        if len(os.listdir(pr_folderpath)) > 0 and scene.startswith("LC08"):
            #grab all the BQA files to calculate the percent cloud
            BQApath = pr_folderpath+scene+"/"+scene+'_BQA_Box'+BoxID+'.TIF'
#             print(BQApath)
            
            #read in your BQA subset raster as a numpy array:
            subsetBQA = mpimg.imread(BQApath)
            
            #CALCULATE % CLOUD COVER USING YOUR BQA SUBSET
            #first, calculate the total number of pixels
            totalpixels = subsetBQA.shape[0]*subsetBQA.shape[1]
            
            #then, calculate the number of cloud pixels:
            #mask for pixels that have a value > than your threshold value
            cloudBQA = subsetBQA[subsetBQA > BQA_thresh]
            
            #calculate number of fill pixels (fill value of 1. Will be less than 2.0)
            fillBQA = subsetBQA[subsetBQA < 2.0]
            
            #and count those cloudpixels and fillpixels:
            cloudpixels = len(cloudBQA); fillpixels = len(fillBQA)
            
            #divide this by the totalpixels and multiply by 100
            cloudpercent = int(float(cloudpixels)/float(totalpixels)*100)
            fillpercent = int(float(fillpixels)/float(totalpixels)*100)
            
            #check that the values are sensible
            print(scene, 'Cloud % ', cloudpercent, 'Fill %', fillpercent)
            
            #set path to rp buffer:
            pathtobuffer_rp = pathtobuffer+"_UTM_"+zone+".shp"
            
            #IF % CLOUD COVER IS LESS THAN OR EQUAL TO YOUR THRESHOLD DOWNLOAD THE BANDS FOR THAT SCENE:
            if cloudpercent <= cpercent_thresh and fillpercent <= fpercent_thresh:
                #download the bands for that scene into your scene folders:
                for band in bands:
                    #make sure the band is in string format:
                    band = str(band)
                    #set input path to your bands in AWS:
                    pathin = '/vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/'+path+"/"+row+"/"+scene+"/"+scene+"_B"+band+".TIF"
                    #set your output path to the overall BoxID folder, not the scene folders
                    pathout = downloadpath+'Box'+BoxID+'/'+scene+"_B"+band+'_Buffer'+BoxID+'.TIF'
                    
                    #set download command and check:
                    download_cmd = 'gdalwarp -cutline '+pathtobuffer_rp+' -crop_to_cutline '+pathin+' '+pathout
#                     download_cmd = 'gdalwarp -cutline '+pathtoshp_rp+' -crop_to_cutline '+pathin+' '+pathout
                    print(download_cmd)
                    
                    #When you're ready, comment out the above print command and
                    #uncomment the following to commence the download:                   
                    subprocess.call(download_cmd, shell=True)
                    print(scene+"_B"+band+'_Buffer'+BoxID+".TIF downloaded")

Box067  EXISTS ALREADY. SKIP.
LC08_L1TP_233018_20181104_20181104_01_RT Cloud %  0 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20181104_20181104_01_RT/LC08_L1TP_233018_20181104_20181104_01_RT_B8.TIF /media/jukes/jukes1/LS8aws/Box067/LC08_L1TP_233018_20181104_20181104_01_RT_B8_Buffer067.TIF
LC08_L1TP_233018_20181104_20181104_01_RT_B8_Buffer067.TIF downloaded
LC08_L1GT_233018_20190312_20190312_01_RT Cloud %  62 Fill % 37
LC08_L1TP_233018_20150621_20170407_01_T1 Cloud %  16 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20150621_20170407_01_T1/LC08_L1TP_233018_20150621_20170407_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box067/LC08_L1TP_233018_20150621_20170407_01_T1_B8_Buffer067.TIF
LC08_L1TP_233018_20150621_201

LC08_L1TP_233018_20180613_20180703_01_T1_B8_Buffer067.TIF downloaded
LC08_L1TP_233018_20140906_20170419_01_T1 Cloud %  0 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20140906_20170419_01_T1/LC08_L1TP_233018_20140906_20170419_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box067/LC08_L1TP_233018_20140906_20170419_01_T1_B8_Buffer067.TIF
LC08_L1TP_233018_20140906_20170419_01_T1_B8_Buffer067.TIF downloaded
LC08_L1TP_233018_20200501_20200509_01_T1 Cloud %  0 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20200501_20200509_01_T1/LC08_L1TP_233018_20200501_20200509_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box067/LC08_L1TP_233018_20200501_20200509_01_T1_B8_Buffer067.TIF
LC08_L1TP_233018_20200501_20200509_01_T1_B8_Buffer067.

LC08_L1TP_233018_20180917_20180928_01_T1_B8_Buffer067.TIF downloaded
LC08_L1TP_233018_20150707_20170407_01_T1 Cloud %  4 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20150707_20170407_01_T1/LC08_L1TP_233018_20150707_20170407_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box067/LC08_L1TP_233018_20150707_20170407_01_T1_B8_Buffer067.TIF
LC08_L1TP_233018_20150707_20170407_01_T1_B8_Buffer067.TIF downloaded
LC08_L1TP_233018_20180205_20180221_01_T1 Cloud %  60 Fill % 37
LC08_L1GT_233018_20180816_20180816_01_RT Cloud %  50 Fill % 37
LC08_L1TP_233018_20190515_20190515_01_RT Cloud %  0 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20190515_20190515_01_RT/LC08_L1TP_233018_20190515_20190515_01_RT_B8.TIF /media/jukes/jukes1/

LC08_L1TP_233018_20200227_20200227_01_RT_B8_Buffer067.TIF downloaded
LC08_L1TP_233018_20180629_20180629_01_RT Cloud %  0 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20180629_20180629_01_RT/LC08_L1TP_233018_20180629_20180629_01_RT_B8.TIF /media/jukes/jukes1/LS8aws/Box067/LC08_L1TP_233018_20180629_20180629_01_RT_B8_Buffer067.TIF
LC08_L1TP_233018_20180629_20180629_01_RT_B8_Buffer067.TIF downloaded
LC08_L1TP_233018_20180309_20180320_01_T1 Cloud %  62 Fill % 37
LC08_L1TP_233018_20181222_20181227_01_T1 Cloud %  62 Fill % 37
LC08_L1TP_233018_20190920_20190920_01_RT Cloud %  0 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20190920_20190920_01_RT/LC08_L1TP_233018_20190920_20190920_01_RT_B8.TIF /media/jukes/jukes1/

LC08_L1TP_233018_20181104_20181115_01_T1_B8_Buffer067.TIF downloaded
LC08_L1TP_233018_20150824_20170405_01_T1 Cloud %  15 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20150824_20170405_01_T1/LC08_L1TP_233018_20150824_20170405_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box067/LC08_L1TP_233018_20150824_20170405_01_T1_B8_Buffer067.TIF
LC08_L1TP_233018_20150824_20170405_01_T1_B8_Buffer067.TIF downloaded
LC08_L1TP_233018_20190328_20190328_01_RT Cloud %  0 Fill % 37
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box067/Buffer067_UTM_23.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/233/018/LC08_L1TP_233018_20190328_20190328_01_RT/LC08_L1TP_233018_20190328_20190328_01_RT_B8.TIF /media/jukes/jukes1/LS8aws/Box067/LC08_L1TP_233018_20190328_20190328_01_RT_B8_Buffer067.TIF
LC08_L1TP_233018_20190328_20190328_01_RT_B8_Buffer067

...

LC08_L1TP_232013_20160429_20170326_01_T1_B8_Buffer301.TIF downloaded
LC08_L1TP_232013_20190727_20190801_01_T1 Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_24.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/232/013/LC08_L1TP_232013_20190727_20190801_01_T1/LC08_L1TP_232013_20190727_20190801_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_232013_20190727_20190801_01_T1_B8_Buffer301.TIF
LC08_L1TP_232013_20190727_20190801_01_T1_B8_Buffer301.TIF downloaded
LC08_L1TP_232013_20180825_20180825_01_RT Cloud %  20 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_24.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/232/013/LC08_L1TP_232013_20180825_20180825_01_RT/LC08_L1TP_232013_20180825_20180825_01_RT_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_232013_20180825_20180825_01_RT_B8_Buffer301.TIF
LC08_L1TP_232013_20180825_20180825_01_RT_B8_Buffer301

LC08_L1TP_230013_20200512_20200512_01_RT_B8_Buffer301.TIF downloaded
LC08_L1TP_230013_20170605_20170616_01_T1 Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_25.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/230/013/LC08_L1TP_230013_20170605_20170616_01_T1/LC08_L1TP_230013_20170605_20170616_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_230013_20170605_20170616_01_T1_B8_Buffer301.TIF
LC08_L1TP_230013_20170605_20170616_01_T1_B8_Buffer301.TIF downloaded
LC08_L1TP_230013_20160415_20170326_01_T1 Cloud %  48 Fill % 51
LC08_L1TP_230013_20180405_20180405_01_RT Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_25.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/230/013/LC08_L1TP_230013_20180405_20180405_01_RT/LC08_L1TP_230013_20180405_20180405_01_RT_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_230013_20180405_20180405_01_RT_B8_Buffe

LC08_L1TP_230013_20150429_20170409_01_T1_B8_Buffer301.TIF downloaded
LC08_L1TP_230013_20180608_20180615_01_T1 Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_25.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/230/013/LC08_L1TP_230013_20180608_20180615_01_T1/LC08_L1TP_230013_20180608_20180615_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_230013_20180608_20180615_01_T1_B8_Buffer301.TIF
LC08_L1TP_230013_20180608_20180615_01_T1_B8_Buffer301.TIF downloaded
LC08_L1TP_230013_20170824_20170913_01_T1 Cloud %  48 Fill % 51
LC08_L1TP_230013_20190713_20190719_01_T1 Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_25.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/230/013/LC08_L1TP_230013_20190713_20190719_01_T1/LC08_L1TP_230013_20190713_20190719_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_230013_20190713_20190719_01_T1_B8_Buffe

LC08_L1GT_230013_20180811_20180811_01_RT_B8_Buffer301.TIF downloaded
LC08_L1TP_230013_20180726_20180731_01_T1 Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_25.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/230/013/LC08_L1TP_230013_20180726_20180731_01_T1/LC08_L1TP_230013_20180726_20180731_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_230013_20180726_20180731_01_T1_B8_Buffer301.TIF
LC08_L1TP_230013_20180726_20180731_01_T1_B8_Buffer301.TIF downloaded
LC08_L1TP_230013_20130829_20170502_01_T1 Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_25.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/230/013/LC08_L1TP_230013_20130829_20170502_01_T1/LC08_L1TP_230013_20130829_20170502_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_230013_20130829_20170502_01_T1_B8_Buffer301.TIF
LC08_L1TP_230013_20130829_20170502_01_T1_B8_Buffer301.

LC08_L1TP_230013_20140325_20170424_01_T1_B8_Buffer301.TIF downloaded
LC08_L1TP_230013_20190510_20190521_01_T1 Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_25.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/230/013/LC08_L1TP_230013_20190510_20190521_01_T1/LC08_L1TP_230013_20190510_20190521_01_T1_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_230013_20190510_20190521_01_T1_B8_Buffer301.TIF
LC08_L1TP_230013_20190510_20190521_01_T1_B8_Buffer301.TIF downloaded
LC08_L1TP_230013_20150616_20170407_01_T1 Cloud %  48 Fill % 51
LC08_L1TP_230013_20190510_20190510_01_RT Cloud %  0 Fill % 51
gdalwarp -cutline /home/jukes/Documents/Sample_glaciers/Box301/Buffer301_UTM_25.shp -crop_to_cutline /vsicurl/https://landsat-pds.s3.amazonaws.com/c1/L8/230/013/LC08_L1TP_230013_20190510_20190510_01_RT/LC08_L1TP_230013_20190510_20190510_01_RT_B8.TIF /media/jukes/jukes1/LS8aws/Box301/LC08_L1TP_230013_20190510_20190510_01_RT_B8_Buffe

### Reproject newly downloaded images into Greenland Polar Stereo projection

In [88]:
# Loop through the BoxIDs in the dataframe with your path row combinations:
for BoxID in list(set(boxes_pr_df.index)):
    # Set output BoxID path 
    bp_out = downloadpath+'Box'+BoxID+'/'
    
    # create output folder to reproject into
    if os.path.exists(bp_out+'reprojected/'):
        print("Box"+BoxID, "Reprojected EXISTS ALREADY.")
    else:
        os.mkdir(bp_out+'reprojected/')
        print("Box"+BoxID+" Reprojected directory made")
                      
    # grab all downloaded images and reproject:
    downloadedimages = os.listdir(bp_out)
    for image in downloadedimages:
        if image.startswith("LC08"):
            imagename = image[:-4]
#             os.remove(bp_out+image) # remove old images
    #         print(imagename)
            rp_cmd = "gdalwarp -t_srs '+proj=stere +lat_ts=7|0 +lat_0=90 +lon_0=-45 +y=0 +x=0 +k=1 +datum=WGS84 +units=m' "+bp_out+image+" "+bp_out+'reprojected/'+imagename+"_PS.TIF"
#             print(rp_cmd)
            subprocess.call(rp_cmd, shell=True)   
    print("Box"+BoxID+" reprojected.")

Box085 Reprojected directory made
Box085 reprojected.
Box121 Reprojected EXISTS ALREADY.
Box121 reprojected.
Box133 Reprojected directory made
Box133 reprojected.
Box151 Reprojected EXISTS ALREADY.
Box151 reprojected.
Box157 Reprojected directory made
Box157 reprojected.
Box115 Reprojected EXISTS ALREADY.
Box115 reprojected.
Box145 Reprojected EXISTS ALREADY.
Box145 reprojected.
Box235 Reprojected EXISTS ALREADY.
Box235 reprojected.
Box259 Reprojected EXISTS ALREADY.
Box259 reprojected.
Box163 Reprojected directory made
Box163 reprojected.
Box265 Reprojected EXISTS ALREADY.
Box265 reprojected.
Box295 Reprojected EXISTS ALREADY.
Box295 reprojected.
Box301 Reprojected directory made
Box301 reprojected.
Box217 Reprojected directory made
Box217 reprojected.
Box271 Reprojected EXISTS ALREADY.
Box271 reprojected.
Box247 Reprojected directory made
Box247 reprojected.
Box175 Reprojected EXISTS ALREADY.
Box175 reprojected.
Box079 Reprojected directory made
Box079 reprojected.
Box223 Reprojected

### Grab the image acquisition dates from the metadata files

In [89]:
import datetime

# create a list of datetime objects for the images:
datetimes = []; scenes_dated = []

# Loop through the dataframe with your path row combinations:
# for index, row in pr_df_multi.iterrows():
for index, row in boxes_pr_df.iterrows():
    path = row['Path']; row = row['Row']; BoxID = index; 
    folder_name = 'Path'+path+'_Row'+row+'_c1'; print(folder_name)
    
    # Output folder paths
    folderpath = downloadpath+folder_name+'/'
    bp_out = downloadpath+'Box'+BoxID+'/reprojected/'
    
    # keep track of the number of scenes:
    scenecount = 0
    
    # list of files in directory where you downloaded images
    downloaded_scenes = os.listdir(bp_out)
    for scene in downloaded_scenes:
        #if it's a downloaded image and in the folder we are working on:
        if scene.endswith('.TIF') and scene.startswith("LC08"):
            scenename = scene[:-20]
            if scenename in os.listdir(folderpath):
                #go into the folder and open the metadata file:
                scenefiles = os.listdir(folderpath+scenename+'/')
                for file in scenefiles:
                    if ("MTL.txt" in file):
                        mdata = open(folderpath+scenename+"/"+scenename+"_MTL.txt", "r")
                        #loop through each line in metadata to find the date (and time) of acquisition
                        for line in mdata:
                            variable = line.split("=")[0]
                            if ("DATE_ACQUIRED" in variable):
                                date = line.split("=")[1][1:-1]

                        #save the date as a datetime object and append to list
                        dates = datetime.datetime.strptime(date, '%Y-%m-%d')
                        datetimes.append(dates); scenes_dated.append(scenename)
                scenecount = scenecount+1

# Store in a dataframe
datetime_df = pd.DataFrame(list(zip(scenes_dated, datetimes)), columns=['Scene', 'datetime'])
datetime_df = datetime_df.sort_values(by='datetime', ascending=True); datetime_df = datetime_df.drop_duplicates()
datetime_df

Path233_Row018_c1
Path232_Row018_c1
Path233_Row018_c1
Path232_Row018_c1
Path233_Row018_c1
Path232_Row018_c1
Path233_Row018_c1
Path232_Row018_c1
Path233_Row018_c1
Path232_Row018_c1
Path001_Row018_c1
Path001_Row017_c1
Path232_Row018_c1
Path233_Row018_c1
Path232_Row018_c1
Path233_Row017_c1
Path233_Row018_c1
Path232_Row018_c1
Path233_Row017_c1
Path232_Row018_c1
Path233_Row017_c1
Path232_Row018_c1
Path233_Row017_c1
Path232_Row017_c1
Path232_Row017_c1
Path233_Row017_c1
Path232_Row017_c1
Path233_Row017_c1
Path232_Row017_c1
Path001_Row017_c1
Path233_Row017_c1
Path232_Row017_c1
Path233_Row017_c1
Path232_Row017_c1
Path233_Row017_c1
Path233_Row017_c1
Path232_Row017_c1
Path233_Row017_c1
Path232_Row017_c1
Path232_Row017_c1
Path233_Row017_c1
Path233_Row017_c1
Path232_Row017_c1
Path232_Row017_c1
Path233_Row017_c1
Path232_Row017_c1
Path233_Row017_c1
Path233_Row016_c1
Path233_Row016_c1
Path001_Row016_c1
Path232_Row016_c1
Path232_Row016_c1
Path233_Row016_c1
Path001_Row016_c1
Path233_Row016_c1
Path001_Ro

Scene   datetime
8014  LC08_L1TP_231014_20130320_20170505_01_T1 2013-03-20
5607  LC08_L1TP_232016_20130402_20170505_01_T1 2013-04-02
7441  LC08_L1TP_232013_20130402_20170505_01_T1 2013-04-02
3273  LC08_L1TP_233017_20130412_20170505_01_T1 2013-04-12
7396  LC08_L1TP_233013_20130412_20170505_01_T1 2013-04-12
...                                        ...        ...
8149  LC08_L1TP_230014_20200512_20200512_01_RT 2020-05-12
8509  LC08_L1TP_230013_20200512_20200526_01_T1 2020-05-12
8503  LC08_L1TP_230013_20200512_20200512_01_RT 2020-05-12
7382  LC08_L1TP_233013_20200602_20200608_01_T1 2020-06-02
7425  LC08_L1TP_233013_20200602_20200602_01_RT 2020-06-02

[1925 rows x 2 columns]

#### Write image dates to a csv file:

In [90]:
# change filename as desired
DATES_NAME = 'imgdates_SE_2.csv'
datetime_df.to_csv(path_or_buf = basepath+DATES_NAME, sep=',')

# 7) Remove cloudy images that slipped through BQA filtering

In [91]:
#convert all files in reprojected folder to png from TIF
for BoxID in BoxIDs:
    print(BoxID)
    command = 'cd '+downloadpath+'Box'+BoxID+'/reprojected/; '+'mogrify -format png *_PS.TIF'
#     print(command)
    subprocess.call(command, shell=True)

067
073
079
085
091
097
103
109
115
121
127
133
139
145
151
157
163
169
175
181
187
193
199
205
211
217
223
229
235
241
247
253
259
265
271
277
283
289
295
301


In [92]:
import cv2

for BoxID in BoxIDs:
    imagepath = downloadpath+'Box'+BoxID+'/reprojected/'
    for img in os.listdir(imagepath):
        if img.endswith('Buffer'+BoxID+'_PS.png'):
            image = cv2.imread(imagepath+img,-1)
            imageplt = mpimg.imread(imagepath+img)
            image_nofill = imageplt[imageplt > 0] # don't consider the fill points
            img_std = np.std(image_nofill)
            if len(image_nofill.shape) > 1:
                img_range = np.max(image_nofill) - np.min(image_nofill)
                img_med = np.median(image_nofill)
    #             print(img, img_std, img_range, img_med)

                if img_std < 0.04 and img_med > 0.15:
                    os.remove(imagepath+img) # remove png mimage
                    os.remove(imagepath+img[:-4]+'.TIF') # remove pgm image
    #                 imgplt_trim = plt.imshow(cv2.cvtColor(imageplt, cv2.COLOR_BGR2RGB))
    #                 plt.show()

### Grab fraction of total images available that were cloudy

In [93]:
# access data using the path row csv file:
boxes_pr_df = pd.read_csv(basepath+'LS_pathrows_SE_2.csv', dtype=str)
boxes_pr_df = boxes_pr_df.set_index('BoxID'); BoxIDs = list(set(boxes_pr_df.index))
print(BoxIDs); boxes_pr_df.head()

['085', '121', '133', '151', '157', '115', '145', '235', '259', '163', '265', '295', '301', '217', '271', '247', '175', '079', '223', '229', '073', '277', '205', '241', '169', '289', '211', '283', '067', '187', '127', '139', '109', '199', '193', '103', '091', '253', '181', '097']


Unnamed: 0 Path  Row Zone
BoxID                          
067            1  233  018   23
067            8  232  018   23
073            2  233  018   23
073            9  232  018   23
079            3  233  018   23

In [94]:
im_tots = []; downloaded = []; fractions = [];

for BoxID in BoxIDs:
    pathrows_BoxID = boxes_pr_df[boxes_pr_df.index == BoxID].copy() # grab path rows for that BoxID
    
    im_tot = 0 # count number of total images
    for idx, rw in pathrows_BoxID.iterrows():
        p = rw['Path']; r = rw['Row']
        ims_pr = len(os.listdir(downloadpath+'Path'+p+'_Row'+r+'_c1')) # grab number of scenes in that pathrow
        im_tot = im_tot + ims_pr
    
    counter = 0
    if im_tot == 0:
        download_frac = np.NaN
    else:
        # find number downloaded (not cloudy) from the BoxID folder
        for file in os.listdir(downloadpath+'Box'+BoxID+'/reprojected/'):
            if file.startswith('LC08') and file.endswith('.png') and 'B8' in file:
                counter = counter + 1
            
        download_frac = int(counter/im_tot*100) # grab fraction downloaded
        
    im_tots.append(im_tot); downloaded.append(counter); fractions.append(download_frac)
    
downloaded_df = pd.DataFrame(list(zip(BoxIDs, im_tots, downloaded, fractions)), columns = ['BoxID', 'Total_ims', 'Downloaded', '%'])
downloaded_df 

BoxID  Total_ims  Downloaded   %
0    085        300         184  61
1    121        393         251  63
2    133        263         176  66
3    151        263         158  60
4    157        263         160  60
5    115        286         193  67
6    145        263         173  65
7    235        321         211  65
8    259        321         211  65
9    163        263         165  62
10   265        218         134  61
11   295        473         321  67
12   301        472         304  64
13   217        340         230  67
14   271        218         146  66
15   247        218         146  66
16   175        263         163  61
17   079        300         190  63
18   223        336         226  67
19   229        439         285  64
20   073        300         188  62
21   277        312         217  69
22   205        348         247  70
23   241        218         155  71
24   169        263         162  61
25   289        482         332  68
26   211        348         228  65
27   283        483         292  60
28   067        300         190  63
29   187        382         256  67
30   127        263         171  65
31   139        434         250  57
32   109        286         184  64
33   199        348         239  68
34   193        348         233  66
35   103        456         299  65
36   091        300         192  64
37   253        218         140  64
38   181        263         159  60
39   097        652         391  59

#### Write information on number of cloudy images to a csv file

In [95]:
# change filenmae as desired
CLOUDY_NAME = 'Images_downloaded_SE_2.csv'
downloaded_df.to_csv(basepath+CLOUDY_NAME, sep=',')

# 8) Calculate weighted average flow direction for each glacier

The following code processes ice velocity rasters to determine each glacier of interest's weighted average flow direction. The rasters are subset using the terminus box shapefile using a GDAL command (**gdalwarp**) with the following syntax:

    gdalwarp -cutline path_to_terminusbox.shp -crop_to_cutline path_to_input_velocity.TIF path_to_output_velocity_at_term###.TIF

In [96]:
for BoxID in BoxIDs:
    terminus_path = basepath+"Box"+BoxID+"/RGI_Box"+BoxID+".shp"  # set path to RGI shapefiles
    vx = 'greenland_vel_mosaic250_vx_v1.tif';vy = 'greenland_vel_mosaic250_vy_v1.tif' # names of velocity files
    
    if os.path.exists(terminus_path) == False: # if the RGI shapefile does not exist
        terminus_path = basepath+"Box"+BoxID+"/Box"+BoxID+".shp"  # set the path to the box shapefile instead       
        #SET output paths
        vx_out = basepath+"Box"+BoxID+"/Box"+BoxID+'_'+vx; vy_out = basepath+"Box"+BoxID+"/Box"+BoxID+'_'+vy; 
    else:
        #SET output paths
        vx_out = basepath+"Box"+BoxID+"/RGI_Box"+BoxID+'_'+vx; vy_out = basepath+"Box"+BoxID+"/RGI_Box"+BoxID+'_'+vy; 
        
    vx_in = basepath+vx; vy_in = basepath+vy #set input paths
        
    #SET velocity subset commands and print to check it
    v_subset1 = 'gdalwarp -cutline '+terminus_path+' -crop_to_cutline '+vx_in+" "+vx_out
    v_subset2 = 'gdalwarp -cutline '+terminus_path+' -crop_to_cutline '+vy_in+" "+vy_out
#         print(v_subset_dir_cmd); print(v_subset_mag_cmd)

    #SUBSET velocity rasters
    subprocess.call(v_subset1, shell=True)
    subprocess.call(v_subset2, shell=True)
    
    print("Box"+BoxID+' done.')

Box085 done.
Box121 done.
Box133 done.
Box151 done.
Box157 done.
Box115 done.
Box145 done.
Box235 done.
Box259 done.
Box163 done.
Box265 done.
Box295 done.
Box301 done.
Box217 done.
Box271 done.
Box247 done.
Box175 done.
Box079 done.
Box223 done.
Box229 done.
Box073 done.
Box277 done.
Box205 done.
Box241 done.
Box169 done.
Box289 done.
Box211 done.
Box283 done.
Box067 done.
Box187 done.
Box127 done.
Box139 done.
Box109 done.
Box199 done.
Box193 done.
Box103 done.
Box091 done.
Box253 done.
Box181 done.
Box097 done.


Next, these subset velocity rasters are opened using the **rasterio** package and read into arrays. They are filtered for anomalous values and the velocity magnitudes are converted into weights. Then the **numpy.average()** function is used to calculated the weighted average flow directions where the flow directions of the pixels where the highest velocities are found are weighted more. 

The resulting average flow direction will be representative of the glacier's main flow. These directions will be used to rotate the images of the glaciers so that their flow is due right.

In [97]:
# CREATE list of glacier average flow directions:
boxes = []; avg_rot = []; max_mag = []; num_cells = []

for BoxID in BoxIDs:
    rot_angles = []; max_magnitudes = []
    
    # READ velocity direction and magnitude data at terminus for each glacier into an array
    vx_name = 'greenland_vel_mosaic250_vx_v1.tif';vy_name = 'greenland_vel_mosaic250_vy_v1.tif'

    rgi_exists = 0
    for file in os.listdir(basepath+"Box"+BoxID):
        if file.startswith('RGI') and "greenland_vel" in file:
            rgi_exists = 1
    if rgi_exists == 1:      
        vx = rasterio.open(basepath+"Box"+BoxID+"/RGI_Box"+BoxID+'_'+vx_name, "r") # RGI
        vy = rasterio.open(basepath+"Box"+BoxID+"/RGI_Box"+BoxID+'_'+vy_name, "r") # RGI
    else:
        vx = rasterio.open(basepath+"Box"+BoxID+"/Box"+BoxID+'_'+vx_name, "r") # box 
        vy = rasterio.open(basepath+"Box"+BoxID+"/Box"+BoxID+'_'+vy_name, "r") # box
         
    vx_array = vx.read(); vy_array = vy.read()
    # remove no data values (-2000000000.0)
    vx_masked = vx_array[vx_array != -2000000000.0]; vy_masked = vy_array[vy_array != -2000000000.0]
        
    # CALCULATE FLOW DIRECTION
    direction = np.arctan2(vy_masked, vx_masked)*180/np.pi; 
#   print(BoxID, direction.max(), direction.min())
    # transform so any negative angles are placed on 0 to 360 scale:
    if len(direction[direction < 0]) > 0:
        direction[direction < 0] = 360.0+direction[direction < 0]
        
    # CALCULATE SPEED
    magnitude = np.sqrt((vx_masked*vx_masked) + (vy_masked*vy_masked)) 
        
    if len(direction) > 0: # if there are velocity values remaining
        # IF THERE ARE DIRECTIONS THAT HAVE A REALLY LARGE RANGE > 250.0 it's probably pointing East
        dir_range = direction.max() - direction.min()
        if dir_range > 200.0 and len(direction[direction >200]): # if large range and values above 200
            direction[direction > 180] = direction[direction > 180] - 360.0 # grab those values on a negative scale
            # CALCULATE the weighted average rotation angle
            # calculate weights (0 - 1) from magnitudes
            mag_range = magnitude.max() - magnitude.min(); stretch = 1/mag_range
            weights = stretch*(magnitude - magnitude.min())
            avg_dir = np.average(direction, weights=weights)
            max_magnitude = magnitude.max()*0.00273973 # conversion to m/d?
#           print("East!", avg_dir)
            if avg_dir < 0:
                avg_dir = avg_dir + 360.0 # transform back to 0 to 360 scale
        else:
            mag_range = magnitude.max() - magnitude.min()
            stretch = 1/mag_range
            weights = stretch*(magnitude - magnitude.min())
            avg_dir = np.average(direction, weights=weights)
    #           print(avg_dir)
            max_magnitude = magnitude.max()*0.00273973 # conversion to m/d?
    else:
        avg_dir = np.NaN ; max_magnitude = np.NaN # no velocities to calculate this with

    # APPEND to lists:
    avg_rot.append(avg_dir); max_mag.append(max_magnitude); boxes.append(BoxID); num_cells.append(len(direction))
        
velocities_df = pd.DataFrame(list(zip(boxes,avg_rot, max_mag, num_cells)), columns=['BoxID','Flow_dir', 'Max_speed', 'Pixels'])
velocities_df = velocities_df.sort_values(by='BoxID')
velocities_df = velocities_df.dropna()

In [98]:
velocities_df

BoxID    Flow_dir  Max_speed  Pixels
28   067  334.340878   1.934648    1724
20   073  338.964087   1.122488    1404
17   079   57.097672   0.095915      47
0    085  330.703131   0.136150     306
36   091   40.629864   0.869106    1073
39   097   18.445810   0.258727     505
35   103  331.748882   0.134582     326
5    115   23.730692   1.798056    2969
1    121  272.830338   1.441556    1151
30   127  348.515791   0.340477     368
2    133   42.645988   1.800916    1623
31   139  259.394844   0.321064     275
6    145   15.698853   0.027876     113
3    151  340.247601   1.056471     424
4    157  253.599274   0.332153      81
9    163   85.982765   0.481148     407
24   169  340.708546   0.206243     181
16   175   59.859917   0.117105      69
38   181   49.734047   0.239806     479
29   187   17.681095   0.570845     574
34   193  300.797417   0.302028     215
33   199  106.473793   0.461889      16
22   205   56.542534   0.105179     318
26   211   88.444565   0.158300      66
13   217   86.553268   0.038563     124
18   223  334.909502   0.020636      54
19   229   92.853615   0.137008     241
7    235  209.207825   0.225594     159
23   241  327.899921   0.088739     341
15   247   28.836479   3.402749    2290
37   253   32.763794   1.113080      28
8    259   60.295387   3.506471    2847
10   265    3.175925   0.172736      14
14   271   73.547363   0.304991      24
21   277  307.169334   0.147524      11
27   283   45.243237   0.140945    1370
25   289  285.856903   1.799771    9542
11   295  343.417818   0.090982     767
12   301  336.923449   0.028731      82

In [112]:
velocities_df = velocities_df.drop(['301', '289', '283' ,'265', '241', '223', '205', '181', '097', '091', '067'])

#### Write glacier velocities to a csv file

In [114]:
# change filename as desired
VEL_NAME = 'Glacier_vel_measures_SE_2.csv'
velocities_df.to_csv(path_or_buf = basepath+VEL_NAME, sep=',')

# 9) Rotate all images by flow direction

Read in the glacier velocity file as velocities_df if not already loaded:

In [100]:
# velocities_df = pd.read_csv(basepath+'Glacier_vel_measures_SE.csv', sep=',', dtype=str)
velocities_df = pd.read_csv(basepath+'Glacier_vel_measures_SE_2.csv', sep=',', dtype=str, usecols=[1,2,3,4])
velocities_df = velocities_df.set_index('BoxID')
velocities_df = velocities_df.dropna()
# velocities_df = velocities_df.drop(['004', '033', '235', '277', '531'])
velocities_df

Flow_dir             Max_speed Pixels
BoxID                                                 
067      334.340877532959    1.9346481993389892   1724
073     338.9640865325928    1.1224878988754272   1404
079     57.09767150878906   0.09591500590286255     47
085     330.7031307220459   0.13614987819480898    306
091     40.62986373901367     0.869105598546753   1073
097    18.445810317993164    0.2587268557157898    505
103     331.7488822937012     0.134582495199852    326
115     23.73069190979004    1.7980555020825195   2969
121    272.83033752441406    1.4415564968249512   1151
127    348.51579093933105   0.34047742073028564    368
133     42.64598846435547    1.8009164664727784   1623
139     259.3948440551758    0.3210638233784485    275
145    15.698853492736816  0.027875998170433045    113
151     340.2476005554199    1.0564707567840577    424
157    253.59927368164062   0.33215273590827943     81
163      85.9827651977539    0.4811484010700989    407
169    340.70854568481445   0.20624254424201965    181
175     59.85991668701172   0.11710508421913148     69
181    49.734046936035156   0.23980597164794923    479
187    17.681095123291016    0.5708449606568909    574
193     300.7974166870117   0.30202820559196475    215
199    106.47379302978516    0.4618888550038147     16
205     56.54253387451172   0.10517867197990417    318
211     88.44456481933594    0.1582999761133194     66
217     86.55326843261719   0.03856322249574661    124
223    334.90950202941895   0.02063572884119034     54
229      92.8536148071289   0.13700787278690338    241
235    209.20782470703125   0.22559381039527893    159
241     327.8999214172363   0.08873923640460968    341
247     28.83647918701172    3.4027486732763674   2290
253      32.7637939453125    1.1130799429714966     28
259    60.295387268066406    3.5064711321069337   2847
265    3.1759252548217773   0.17273576255981446     14
271        73.54736328125   0.30499125769981383     24
277     307.1693344116211   0.14752424545749665     11
283     45.24323654174805   0.14094548217258454   1370
289     285.8569030761719    1.7997713449493409   9542
295      343.417818069458   0.09098177998966217    767
301    336.92344856262207  0.028731408693304063     82

In [101]:
#make directory for rotated images in BoxID folders if it doesn't already exist
for index, row in velocities_df.iterrows():
    BoxID = index
    if os.path.exists(downloadpath+"Box"+BoxID+'/rotated_c1/'):
        print("Already exists.")
#         shutil.rmtree(downloadpath+"Box"+BoxID+'/reprojected/') # DELETE ROTATED IMAGES
        #OTHERWISE, create the folder and download into it
    else:
        os.mkdir(downloadpath+"Box"+BoxID+'/rotated_c1/')
        print("Folder made for Box"+BoxID)

Folder made for Box067
Folder made for Box073
Folder made for Box079
Folder made for Box085
Folder made for Box091
Folder made for Box097
Folder made for Box103
Folder made for Box115
Folder made for Box121
Folder made for Box127
Folder made for Box133
Folder made for Box139
Folder made for Box145
Folder made for Box151
Folder made for Box157
Folder made for Box163
Folder made for Box169
Folder made for Box175
Folder made for Box181
Folder made for Box187
Folder made for Box193
Folder made for Box199
Folder made for Box205
Folder made for Box211
Folder made for Box217
Folder made for Box223
Folder made for Box229
Already exists.
Folder made for Box241
Folder made for Box247
Folder made for Box253
Already exists.
Folder made for Box265
Folder made for Box271
Already exists.
Folder made for Box283
Folder made for Box289
Folder made for Box295
Folder made for Box301


In [102]:
# move rasterized terminus box into reprojected folder:
for index, row in velocities_df.iterrows():
    BoxID = index
    boxfile = 'Box'+BoxID+'_raster_cut.TIF'
    boxrasterpath = basepath+'Box'+BoxID+'/'+boxfile
    newpath = downloadpath+'Box'+BoxID+'/reprojected/'+boxfile
    shutil.copyfile(boxrasterpath, newpath)

In [106]:
# convert all images to png
for index, row in velocities_df.iterrows():
    BoxID = index
    command = 'cd '+downloadpath+'Box'+BoxID+'/reprojected/; '+'mogrify -format png *.TIF'
#     print(command)
    subprocess.call(command, shell=True)

In [107]:
# ROTATE THE IMAGES IF VELOCITIES ARE GOOD
for index, row in velocities_df.iterrows():
    BoxID = index
    print(BoxID)
    # for each file in the reprojected folder:
    for file in os.listdir(downloadpath+"Box"+BoxID+'/reprojected/'):
        if file.endswith('.png'):
            img  = Image.open(downloadpath+"Box"+BoxID+'/reprojected/'+file)
            rotated = img.rotate(-float(row['Flow_dir']))
            rotated.save(downloadpath+"Box"+BoxID+'/rotated_c1/R_'+file)

067
073
079
085
091
097
103
115
121
127
133
139
145
151
157
163
169
175
181
187
193
199
205
211
217
223
229
235
241
247
253
259
265
271
277
283
289
295
301


# 10) Resize all images to the same size (the minimum image size) 

Uses the function resize_pngs which resizes all png files within a folder to the minimum image dimensions found. Centers images when cropping around the edges.

In [108]:
for index, row in velocities_df.iterrows():
    BoxID = index
    print(BoxID)
    resizepath = downloadpath+"Box"+BoxID+'/rotated_c1/'
    resize_pngs(resizepath)

067
073
079
085
091
097
103
115
121
127
133
139
145
151
157
163
169
175
181
187
193
199
205
211
217
223
229
235
241
247
253
259
265
271
277
283
289
295
301


#### Convert these any png images to pgm for Xsmurf analysis:

In [109]:
# convert all final files to pgm
for index, row in velocities_df.iterrows():
    BoxID = index
    command = 'cd '+downloadpath+'Box'+BoxID+'/rotated_c1/; '+'mogrify -depth 16 -format pgm *.png'
    subprocess.call(command, shell=True)

In [22]:
# # rename the rasterized terminus box files if necessary
# for index, row in velocities_df.iterrows():
#     BoxID = index
#     files = os.listdir(downloadpath+'Box'+BoxID+'/rotated_c1/')
#     for file in files:
#         if file.startswith('R_Box'+BoxID+'_cut'):
#             rpath = downloadpath+'Box'+BoxID+'/rotated_c1/'
#             os.rename(rpath+file, rpath+'R_Box'+BoxID+'_raster_cut'+file[-4:])